## AutoRAG의 Data Creation
### AutoRAG의 작동 원리

1. 사용자 질문과 관련 문서를 입력받습니다.
2. 다양한 검색기와 LLM 조합으로 RAG 파이프라인을 구축합니다.
3. 각 파이프라인의 성능을 평가하여 최적의 조합을 찾습니다.
4. 최적화된 RAG 파이프라인을 출력합니다.

### AutoRAG의 장점

- RAG 파이프라인 구축 및 최적화 작업을 자동화합니다.
- 시간과 노력을 절약할 수 있습니다.
- 최적의 RAG 파이프라인을 찾아 AI 답변의 정확성을 높일 수 있습니다.

AutoRAG는 RAG 기술의 활용을 더욱 쉽게 만들어주는 유용한 도구로, RAG 기반 AI 시스템의 성능 향상에 기여할 것으로 기대됩니다!

AutoRAG를 위해서는 RAG의 성능 평가가 필수적이고, RAG의 성능을 평가하려면 data가 필요한데, 대부분의 경우 만족스러운 data가 거의 또는 전혀 없습니다. 하지만, LLM 등장 이후 합성 데이터를 만드는 것이 좋은 대안으로 떠올랐습니다.
![](./image/image0.png)
AutoRAG를 위해서는 사진과 같은 과정을 거쳐 raw data를 `corpus data`, `qa data`로 변환해야 합니다.

In [1]:
# API 키를 환경변수로 관리하기 위한 설정 파일
from dotenv import load_dotenv

# API 키 정보 로드
load_dotenv()

# LangSmith 비활성화
import os
os.environ["LANGCHAIN_TRACING_V2"] = "false"
os.environ["LANGCHAIN_ENDPOINT"] = ""
os.environ["LANGCHAIN_API_KEY"] = ""

## Dataset Format
AutoRAG에 사용되는 dataset은 corpus data, qa data 2가지가 있습니다.

corpus dataset은 RAG 시스템의 정보 검색 단계에서, qa dataset은 답변 생성 및 평가 단계에서 주로 활용됩니다.

두 데이터셋의 질과 양이 RAG 시스템 전체의 성능을 좌우하게 됩니다.

### 1. QA dataset
qa data는 qid, query, retrieval_gt, generation_gt 총 4가지 column을 가집니다.

qid : string

- 각 쿼리의 고유 식별자

query : string

- 사용자의 질문 내용

retrieval_gt : 2D list

- 검색된 정답 ID를 저장하는 문서 ID의 2차원 리스트 (1차원 string도 가능)

- 2차원 리스트인 이유는 질문에 대한 답변을 구성하기 위해 여러 문서의 정보를 조합해야 하기 때문

- 예를 들어 retrieval_gt = [['NewJeans1', 'Aespa1'], ['NewJeans2', 'Aespa2']]라면:

 'NewJeans1'과 'Aespa1' 문서를 참고하거나

 'NewJeans2'와 'Aespa2' 문서를 참고하면해당 질문에 대한 답변을 구성할 수 있다는 의미.

- AutoRAG는 이 column을 사용하여 검색 성능을 평가하기 때문에 매우 중요합니다.

generation_gt : list

- LLM 모델이 생성할 것으로 기대하는 정답 목록입니다.

- RAG 시스템의 Generation 단계에서 목표로 하는 이상적인 답변 텍스트를 의미하며, 시스템 평가 및 학습을 위한 지표로 활용됩니다.



### 2. Corpus dataset
corpus dataset은 doc_id, contents, metadata 총 3가지 column을 가집니다.

doc_id : string

- chunk된 각 passage의 고유 식별자

contents : string

- 실제 콘텐츠 내용

- 다양한 chunk 전략을 통해 chunk된 결과물

metadata : dictionary

- chunk된 각 passage의 metadata 모음

### evaluation data 생성
이제, corpus data와 qa data를 직접 생성해보겠습니다!

저는 네이버에서 적당한 길이의 뉴스기사 .txt 파일로 만들어서 데이터로 사용해보았습니다.

### raw data에서 → corpus data 생성하기
1. llama_index, LangChain 등의 loader를 이용해서 raw data를 texts로 load

2. texts를 여러 문단으로 split

3. corpus data로 만들기

- llama index는 llama_document_to_parquet, llama_text_node_to_parquet

- Langchain은 langchain_document_to_parquet 사용

In [2]:
import os
from langchain_upstage import UpstageLayoutAnalysisLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from autorag.data.corpus import langchain_documents_to_parquet
from rainbow_html_transformer import HTMLToTextWithIndentation
from langchain.schema import Document

# PDF 파일이 있는 디렉토리 경로
pdf_directory = "raw_docs/"
txt_directory = "processed_txt/"

# 디렉토리가 없으면 생성
os.makedirs(txt_directory, exist_ok=True)

# HTML 문서를 텍스트로 변환하는 변환기 생성
html_transformer = HTMLToTextWithIndentation()

# 모든 문서를 저장할 리스트
all_documents = []

# 디렉토리 내의 모든 PDF 파일 처리
for filename in os.listdir(pdf_directory):
    if filename.endswith(".pdf"):
        pdf_path = os.path.join(pdf_directory, filename)
        loader = UpstageLayoutAnalysisLoader(
            pdf_path, 
            split="page",
            exclude=["annotations"]  # 주석을 제외하도록 설정
        )
        documents = loader.load()
        
        # PDF 파일명으로 txt 파일명 생성
        txt_filename = f"{os.path.splitext(filename)[0]}.txt"
        txt_path = os.path.join(txt_directory, txt_filename)
        
        # 모든 페이지의 내용을 하나의 문자열로 결합
        full_content = ""
        
        for doc in documents:
            transformed_doc = html_transformer.transform_documents([doc])[0]
            full_content += transformed_doc.page_content + "\n\n"  # 페이지 사이에 빈 줄 추가
        
        # 전체 내용을 하나의 txt 파일로 저장
        with open(txt_path, 'w', encoding='utf-8') as f:
            f.write(full_content)
        
        # 전체 내용을 하나의 Document 객체로 생성
        all_documents.append(Document(page_content=full_content, metadata={'source': txt_path}))
        
        print(f"{filename}: {len(documents)} 페이지 처리 및 저장 완료")

print(f"총 처리된 문서의 수: {len(all_documents)}")

# 텍스트 분할
text_splitter = RecursiveCharacterTextSplitter(chunk_size=512, chunk_overlap=128)
split_documents = text_splitter.split_documents(all_documents)

print(f"분할 후 문서의 수: {len(split_documents)}")

# Parquet 파일로 변환
corpus_df = langchain_documents_to_parquet(split_documents,     
                                           upsert=True,  # 기존 파일이 있으면 덮어쓰기
                                           output_filepath='./new_data/corpus.parquet')

print("Parquet 파일 생성 완료")
corpus_df.head()

/home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/pydantic/_internal/_fields.py:161: UserWarning: Field "model_id" has conflict with protected namespace "model_".

You may be able to resolve this warning by setting `model_config['protected_namespaces'] = ()`.
  warnings.warn(


판매약관_신한간편가입큐브종합건강보장보험(무배당, 해약환급금 미지급형)_240503_수정_P1618.pdf: 1542 페이지 처리 및 저장 완료
사업방법서_신한간편가입큐브종합건강보장보험(무배당, 해약환급금 미지급형)_20240503_P23.pdf: 23 페이지 처리 및 저장 완료
상품요약서_신한간편가입큐브종합건강보장보험(무배당, 해약환급금 미지급형)_20240503_P68.pdf: 68 페이지 처리 및 저장 완료
총 처리된 문서의 수: 3
분할 후 문서의 수: 1045
Parquet 파일 생성 완료


doc_id  \
0  881051ee-6ca7-4d7a-9d73-9888257f5c2c   
1  d5373fa5-7100-4d73-851e-5a42a83401b5   
2  7aee205f-2563-445a-b71c-76a7b5b2498b   
3  3af85382-db0e-4877-b9eb-fab26058eb36   
4  16d01c75-cda7-4e2a-8f16-a7e706238772   

                                            contents  \
0  C9999999\n\nC9999999\n\n#### 21674001\n\n21674...   
1  ### (무배당, 해약환급\n\n(무배당, 해약환급\n\nC2932001\n\nC2...   
2  C2964001\n\nC2964001\n\nC2972001\n\nC2972001\n...   
3  C2560001\n\nC2560001\n\nC2568001\n\nC2568001\n...   
4  약관 가이드북 15약관 요약서 19주요 보험용어 해설 37가입부터 지급까지 쉽게 찾...   

                                            metadata  
0  {'source': 'processed_txt/판매약관_신한간편가입큐브종합건강보장보...  
1  {'source': 'processed_txt/판매약관_신한간편가입큐브종합건강보장보...  
2  {'source': 'processed_txt/판매약관_신한간편가입큐브종합건강보장보...  
3  {'source': 'processed_txt/판매약관_신한간편가입큐브종합건강보장보...  
4  {'source': 'processed_txt/판매약관_신한간편가입큐브종합건강보장보...

생성된 data를 잘 살펴보면, corpus dataset의 column 요소인 `doc_id`, `contents`, `metadata` 가 모두 생성된 것을 확인할 수 있습니다.

### corpus data에서 → qa data 생성하기

- `generate_qa_llama_index`는 콘텐츠별로 query 와 generation_gt 를 생성해줍니다.

- `question_num_per_content` 매개변수를 변경하여 콘텐츠 당 생성할 질문 개수를 설정할 수 있습니다 .

- `make_single_content_qa`함수는 `qa.parquet`파일을 생성합니다.

In [3]:
print(corpus_df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1045 entries, 0 to 1044
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   doc_id    1045 non-null   object
 1   contents  1045 non-null   object
 2   metadata  1045 non-null   object
dtypes: object(3)
memory usage: 24.6+ KB
None


In [9]:
import logging
logging.getLogger("openai").setLevel(logging.WARNING)
logging.getLogger("httpx").setLevel(logging.WARNING)
logging.getLogger("langchain").setLevel(logging.ERROR)

import pandas as pd
# 라마인덱스 LLM 사용   
from llama_index.llms.openai import OpenAI
# 라마인덱스 업스테이지 LLM 사용
# from llama_index.llms.upstage import Upstage
from autorag.data.qacreation import generate_qa_llama_index, make_single_content_qa
import nest_asyncio

nest_asyncio.apply()

# corpus_df = pd.read_parquet('./new_data/corpus.parquet')
llm = OpenAI(model='gpt-3.5-turbo', temperature=1.0)
# llm = Upstage(temperature=1.0)

# corpus_df의 전체 행 수를 사용
total_rows = len(corpus_df)

# 사용자 정의 프롬프트
prompt = """
주어진 보험상품 관련 사업방법서와 상품요약서 문장 내용을 참조해서 질문과 답변 쌍으로 생성해 주시고,
생성하는 질문과 답변은 반듯이 한국어로 생성되게 해주세요.

문장:
{{text}}

Number of questions to generate: {{num_questions}}

Example:
[Q]: 신한간편가입큐브종합건강보장보험(무배당, 해약환급금 미지급형)의 보험종목의 명칭은 무엇인가?
[A]: 일반형, 신한큐브종합건강보장보험(무배당).

Result:
"""

qa_df = make_single_content_qa(
    corpus_df, 
    total_rows,  # corpus_df의 모든 행을 사용
    generate_qa_llama_index, 
    llm=llm,
    prompt=prompt,  
    question_num_per_content=1,
    output_filepath='./new_data/qa.parquet',
    upsert=True  # 기존 파일이 있으면 덮어쓰기
)

print(f"생성된 QA 쌍의 수: {len(qa_df)}")
qa_df.head()

23it [06:42, 16.24s/it]/home/samuel/.pyenv/versions/3.11.1/lib/python3.11/typing.py:370: RuntimeWarning: coroutine 'async_qa_gen_llama_index' was never awaited
  ev_args = tuple(_eval_type(a, globalns, localns, recursive_guard) for a in t.__args__)
33it [09:42, 17.66s/it]

생성된 QA 쌍의 수: 1045


retrieval_gt  \
0  [[3fe5fce0-48b7-40d9-b37f-546272c33dba]]   
1  [[bbb410bf-6d7d-4846-a9d0-7d3ae07595ad]]   
2  [[4531329a-03fa-455b-99ee-b0074a340809]]   
3  [[34a8f74d-607d-4b3c-8a39-0035a799759d]]   
4  [[3a37c018-88be-43bd-9344-0ad07d1b4f66]]   

                                    qid  \
0  ff0c77b5-97f4-4487-8dc4-9910f13f8941   
1  d01cf9fa-793e-4448-850a-bc51360742d2   
2  5be036d7-1ff3-4b35-b3f4-b9de0d3f1a1b   
3  3f4326ee-22f9-4632-989b-3251b46e7946   
4  97d763fb-0a43-4dce-8266-a46ad78bec5a   

                                               query  \
0  뇌출혈진단특약(무배당, 해약환급금 미지급형)의 지급사유가 발생하지 않아 더 이상 보...   
1  신한간편가입큐브종합건강보장보험(무배당, 해약환급금 미지급형)의 가입금액 기준은 어떻...   
2  보험금 지급기간 중 사망하였을 경우나 주계약이 해지되었을 때 발생하는 경우에 대한 ...   
3                            어떤 경우에는 질병의심소견이란 해당하는가?   
4                   다음 상품의 피보험자로 지정할 수 있는 대상은 누구인가요?   

                                       generation_gt  
0  [이 특약은 그때부터 효력이 없습니다. 다만, 취소 또는 철회된 경우에는 주계약이 ...  
1                              [100만원. (가입금액 100만원)]  
2  [해당 특약은 그때부터 효력이 없으며, 회사가 적립한 사망당시의 계약자 적립액을 보...  
3  [의사가 진단서나 소견서 또는 진료의뢰서 등을 서면으로 소견서 포함하여 교부한 경우...  
4               [단체의 규약에서 명시된 상속인이나 피보험자가 될 수 있습니다.]

In [10]:
qa_df.to_csv('./new_data/qa.csv', index=False)

qa.parquet 결과를 보면, 질문이 한국어로 생성된 것을 확인할 수 있습니다.

생성된 data를 잘 살펴보면, qa dataset의 column 요소인 `qid`, `query`, `retrieval_gt`, `generation_gt`가 모두 생성된 것을 확인할 수 있습니다.

## RAGAS evaluation data 생성
RAGAS(RAG Assessment)는 RAG(Retrieval-Augmented Generation) 파이프라인의 성능을 평가하고 모니터링하는 프레임워크입니다!

RAGAS는 평가용 evaluation data를 생성하는 기능도 가지고 있습니다.

### RAGAS를 이용해서 Corpus data에서 → QA set 생성하기
QA set은 RAGAS를 이용해서도 생성할 수 있습니다.

### RAGAS 질문 유형
RAGAS는 원본 질문을 변형하여 추론, 조건, 다중 문맥, 대화형 등 다양한 특성을 가진 복잡한 질문을 생성합니다.

이를 통해 RAG 시스템의 전반적인 성능을 포괄적으로 평가할 수 있습니다.

- simple

>> - RAGAS는 난이도를 혼합하기 위해 단순한 직접적인 질문도 포함합니다.

>> - 예시

>>>> - "뉴턴의 제2법칙은 무엇인가?”

- reasoning (추론)

>> - 원본 질문을 효과적으로 답변하기 위해 추론이 필요하도록 재구성한 질문입니다. RAG 시스템의 multi-step 추론 능력을 평가합니다.

>> - 예시

>>>> - 원본 질문: "미국의 수도는 어디인가?"

>>>> - 추론 질문: "워싱턴 D.C.는 미국의 수도이다. 이 도시는 어떤 강 근처에 위치하는가?"

- multi_context

>> - 답변을 구성하기 위해 여러 관련 섹션이나 텍스트 조각의 정보가 필요하도록 재구성한 질문입니다. 검색 컴포넌트가 모든 관련 문맥을 찾아내는 능력을 평가합니다.

>> - 예시

>>>> - 원본 질문: "암은 무엇인가?"

>>>> - 다중 문맥 질문: "암의 원인, 증상 및 치료법에 대해 설명하시오."

- conditional

>> - 원본 질문에 조건을 추가하여 복잡성을 높인 질문입니다. RAG 시스템이 조건을 처리하는 능력을 평가합니다.

>> - 예시

>>>> - 원본 질문: "인간 면역 결핍 바이러스는 무엇인가?"

>>>> - 조건부 질문: "만약 HIV 바이러스에 감염되었다면, 어떤 증상이 나타날 수 있는가?"

### 사용자 정의 모델 사용
RAGAS는 Langchain을 사용하여 사용자 정의 모델을 지원합니다. 

ChatModel또한 Langchain의 클래스를 사용해야 할 수도 있습니다 .

In [6]:
# import pandas as pd
# from ragas.testset.evolutions import simple, reasoning, multi_context, conditional
# from autorag.data.qacreation.ragas import generate_qa_ragas
# from langchain_openai import ChatOpenAI, OpenAIEmbeddings


# corpus_df = pd.read_parquet('new_data/corpus.parquet')

# distributions = {  # uniform distribution
#     simple: 0.25,
#     reasoning: 0.25,
#     multi_context: 0.25,
#     conditional: 0.25
# }
# generator_llm = ChatOpenAI(model="gpt-3.5-turbo", temperature=0.4)
# critic_llm = ChatOpenAI(model="gpt-4o", temperature=0.0)
# embedding_model = OpenAIEmbeddings()

# qa_df = generate_qa_ragas(corpus_df.iloc[1:6], test_size=2, distributions=distributions,
#                           generator_llm=generator_llm, critic_llm=critic_llm, embedding_model=embedding_model)

# qa_df.head()

embedding nodes:   0%|          | 0/14 [00:00<?, ?it/s]

Generating:   0%|          | 0/2 [00:00<?, ?it/s]

[08/22/24 14:03:06] INFO     [evolutions.py:117] >> retrying evolution: 0 times                   ]8;id=570068;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py\evolutions.py]8;;\:]8;id=539249;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py#117\117]8;;\

[08/22/24 14:03:07] INFO     [evolutions.py:117] >> retrying evolution: 0 times                   ]8;id=951030;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py\evolutions.py]8;;\:]8;id=228257;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py#117\117]8;;\

[08/22/24 14:03:08] INFO     [evolutions.py:117] >> retrying evolution: 0 times                   ]8;id=146346;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py\evolutions.py]8;;\:]8;id=765247;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py#117\117]8;;\

...

[08/22/24 14:05:31] INFO     [evolutions.py:323] >> rewritten question: What is the role of       ]8;id=879913;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py\evolutions.py]8;;\:]8;id=403949;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py#323\323]8;;\
                             "\uc2e0\ud55c\ud050\ube0c\uc885\ud569\uac74\uac15\ubcf4\uc7a5\ubcf4\                  
                             ud5d8" in the process of "\ud574\uc57d\ud658\uae09\uae08                              
                             \ubbf8\uc9c0\uae09\ud615"?                                                            

[08/22/24 14:05:40] INFO     [evolutions.py:406] >> rewritten question: "What is the function of  ]8;id=161723;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py\evolutions.py]8;;\:]8;id=31693;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py#406\406]8;;\
                             \"\\uc2e0\\ud55c\\ud050\\ube0c\\uc885\\ud569\\uac74\\uac15\\ubcf4\\u                  
                             c7a5\\ubcf4\\ud5d8\" in the process of                                                
                             \"\\ud574\\uc57d\\ud658\\uae09\\uae08 \\ubbf8\\uc9c0\\uae09\\ud615\"                  
                             under normal circumstances?"                                                          

[08/22/24 14:05:42] INFO     [evolutions.py:117] >> retrying evolution: 6 times                   ]8;id=340454;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py\evolutions.py]8;;\:]8;id=598309;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/testset/evolutions.py#117\117]8;;\

                    WARNING  [executor.py:57] >> max retries exceeded for                            ]8;id=164859;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/executor.py\executor.py]8;;\:]8;id=553681;file:///home/samuel/Dev/RAG/AutoRAG-tutorial-ko/venv/lib/python3.11/site-packages/ragas/executor.py#57\57]8;;\
                             ConditionalEvolution(generator_llm=LangchainLLMWrapper(run_config=RunCo               
                             nfig(timeout=180, max_retries=15, max_wait=90, max_workers=16,                        
                             exception_types=<class 'openai.RateLimitError'>, log_tenacity=False,                  
                             seed=42)),                                                                            
                             docstore=InMemoryDocumentStore(splitter=<langchain_text_splitters.base.               
                             TokenTextSplitter object at 0x7fd7ef4d7750>,                                          
                             nodes=[Node(metadata={'filename':                                                     
                             '31cfe943-6bb9-499f-93b6-4a7d2d71a1f7', 'last_modified_datetime':                     
                             datetime.datetime(2024, 8, 22, 13, 52, 34, 878296), 'source':                         
                             'processed_txt/027.사업방법서_신한큐브종합건강보장보험(무배당,                        
                             해약환급금 미지급형)_240401_v2_문구수정(1)_P11.txt'},                                 
                             page_content='사업방법서 별지 신한큐브종합건강보장보험(무배당,                        
                             해약환급금 미지급형) １. 보험종목의 명칭 | 0 | 1 |                                    
                             |:------------------------------------------------------|:-------------               
                             -------| | 명칭 | 보험종목 | | 신한큐브종합건강보장보험(무배당,                       
                             해약환급금 미지급형) | 해약환급금 미지급형 | |                                        
                             신한큐브종합건강보장보험(무배당) | 일반형 | ㈜ 1. 다만, “일반형”의 경우               
                             “해약환급금 미지급형”과 동일한 보장내용으로 해약환급금 산출시 해지율을                
                             적용하지 않 은 상품이며, 당사에서 판매하지 않고 “해약환급금 미지급형”과               
                             비교·안내를 위한 종목으로 운영한다. 2. 통신판매채널 판매시 보험종목의                 
                             명칭은 “신한올터치종합건강보장보험(무배당, 해약환급금 미지급형)”으로                  
                             한다. ※ 통신판매채널은 대면영업을 병행하지 않는 아웃바운드TM 및                       
                             인바운드TM을 의미한다. 2. 보험기간, 보험료 납입기간, 피보험자 가입나이                
                             및 보험료 납입주기 | 0 | 1',                                                          
                             doc_id='76048248-421b-44f1-a158-b16922822068', wins=7),                               
                             Node(metadata={'filename': '843de4fa-cc32-490d-87f0-2276cb734c3c',                    
                             'last_modified_datetime': datetime.datetime(2024, 8, 22, 13, 52, 34,                  
                             878301), 'source':                                                                    
                             'processed_txt/027.사업방법서_신한큐브종합건강보장보험(무배당,                        
                             해약환급금 미지급형)_240401_v2_문구수정(1)_P11.txt'},                                 
                             page_content='해약환급금 미지급형)”으로 한다. ※ 통신판매채널은                        
                             대면영업을 병행하지 않는 아웃바운드TM 및 인바운드TM을 의미한다. 2.                    
                             보험기간, 보험료 납입기간, 피보험자 가입나이 및 보험료 납입주기 | 0 | 1               
                             | 2 | 3 | 4 | 5 | 6 |                                                                 
                             |:--------------|:--------------|:--------------|:---------------------               
   

qid  \
0  c5c3675b-9e94-4a5d-899f-c79c7db9400e   

                                               query  \
0  How does evaporation affect the water cycle, w...   

                                       generation_gt  \
0  [The answer to given question is not present i...   

                               retrieval_gt  
0  [[be7057d3-7344-407d-b6c9-163d5728f995]]